In [1]:
import pandas as pd
import numpy as np
import os, sys, json, argparse, pickle
import sumolib, traci
from tqdm import tqdm
from datetime import datetime
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_scr = os.path.join(path_root, 'scripts')
sys.path.append(path_scr)
from generate_signals import SignalGenerator

In [2]:
time_str = '2024-07-29 9:36:32'
time_dt = datetime.strptime(time_str, '%Y-%m-%d %H:%M:%S')
print(time_dt)
time_unix = int(time_dt.timestamp())
print(time_unix)
print(datetime.fromtimestamp(time_unix))

2024-07-29 09:36:32
1722213392
2024-07-29 09:36:32


In [3]:
self = SignalGenerator(config_name='test_0731',
                       file_net='new_sungnam_network_internal_target_0721.net.xml',
                       month=7,
                       day=31,
                       hour=9,
                       minute=5)

In [4]:
self.load_networks()

1-1. 네트워크가 로드되었습니다.


In [5]:
self.load_tables()

1-2. 테이블들이 로드되었습니다.


In [6]:
print(self.history.end_unix.min())
print(self.history.end_unix.max())
print(self.present_time)
print(self.midnight)
print(self.next_day)

1722383967
1722385038
1722384300
1722351600
1722438000


In [7]:
# dura_As = [f'dura_A{i}' for i in range(1,9)]
# dura_Bs = [f'dura_B{i}' for i in range(1,9)]
# for i, row in self.plan.iterrows():
#     is_zero_A = (row[dura_As]==0).all()
#     is_zero_B = (row[dura_Bs]==0).all()
#     assert not (is_zero_A & is_zero_B)
#     if is_zero_B:
#         for j in range(1, 9):
#             self.plan.at[i, f'dura_B{j}'] = row[f'dura_A{j}']
#     if is_zero_A:
#         for j in range(1, 9):
#             self.plan.at[i, f'dura_A{j}'] = row[f'dura_B{j}']

In [8]:
self.prepare_auxiliaries()

1-5. 필요한 보조 객체들이 모두 준비되었습니다.


In [9]:
self.process_history()

2. 신호이력 테이블을 변환합니다.


In [10]:
phases = pd.read_csv(os.path.join(self.path_tables, 'TL_IF_SIGL.csv'))
phases = phases.drop(columns=['FRST_REG_DT', 'RINGA_FLOW', 'RINGB_FLOW'])
phases = phases.rename(columns={
    'PHASE_DT':'start_unix','CRSRD_ID':'inter_no',
    'RINGA_PHASE':'phas_A', 'RINGB_PHASE':'phas_B',
    'MAP_MODE':'STOS_NO'
    })
isp2move_A = self.isp2move['A']
isp2move_B = self.isp2move['B']
phases['move_A'] = phases.apply(
    lambda row: int(isp2move_A.get((row.inter_no, row.STOS_NO, row.phas_A), -1)), axis=1)
phases['move_B'] = phases.apply(
    lambda row: int(isp2move_B.get((row.inter_no, row.STOS_NO, row.phas_B), -1)), axis=1)
phases['start_unix'] = phases['start_unix'].apply(lambda x:int(datetime.strptime(x, '%Y-%m-%d %H:%M:%S').timestamp()))
phases = phases[phases.inter_no.isin(self.inter_nos)].reset_index(drop=True)
phases = phases.drop(columns='STOS_NO')

# - 아래 절차를 5초마다 반복
fsecs = list(range(self.present_time - self.sim_timespan, self.present_time + 1, 5))
for fsec in range(self.present_time - self.sim_timespan, self.present_time + 1, 5): # fsec : unix time by Five SECond
    # 1. 상태 테이블 조회해서 전체 데이터중 필요데이터(교차로번호, A링 현시번호, A링 이동류번호, B링 현시번호, B링 이동류번호)만 수집 : A
    moves = [group.iloc[-1:] for _, group in phases[phases.start_unix <= fsec].groupby('inter_no')]
    if not moves:
        move = pd.DataFrame({'start_unix':[], 'inter_no':[], 'phas_A':[], 'phas_B':[], 'move_A':[], 'move_B':[]})
        pass
    else:
        move = pd.concat(moves)
    move = move.drop(columns='start_unix')
    # move = pd.read_csv(os.path.join(self.path_tables, 'move', f'move_{fsec}.csv'))
    # 2. 이력 테이블 조회해서 교차로별로 유닉스시간 최대인 데이터(교차로번호, 종료유닉스타임)만 수집 : B
    recent_histories = [group.iloc[-1:] for _, group in self.history[self.history['end_unix'] < fsec].groupby('inter_no')] # 교차로별로 유닉스시간이 최대인 행들

    if not recent_histories:
        rhistory = pd.DataFrame({'inter_no':[], 'end_unix':[]}) # recent history
    else:
        rhistory = pd.concat(recent_histories)
    recent_unix = rhistory[['inter_no', 'end_unix']]
    # 3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
    move = pd.merge(move, recent_unix, how='left', on='inter_no')
    # move['end_unix'] = move['end_unix'].fillna(0).astype(int)
    # 4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거
    move = move.rename(columns = {'end_unix':'start_unix'})
    # 5. 이동류 이력정보 READ
    #     - CSV 파일로 서버에 저장된 이동류정보를 읽어옴(파일이 없는 경우에는 데이터가 없는 프레임 D 생성)
    try:
        movement # movement가 존재할 경우 그걸 그대로 씀.
    except NameError: # movement가 존재하지 않는 경우 생성
        movement = pd.DataFrame()
    # 6. 이동류 이력정보 데이터테이블(D)에 C데이터 add
    movement = pd.concat([movement, move])
    # 7. D데이터 프레임에서 중복데이터 제거(교차로번호, 시작 유닉스타임, A링 현시번호, B링 현시번호 같은 행은 제거)
    movement = movement.drop_duplicates(['inter_no','phas_A','phas_B','start_unix'])
    # # 8. D데이터 보관 시간 기준시간을 시작 유닉스 타임의 최대값 - self.subtractor // 2을 값으로 산출하고, 보관 시간 기준시간보다 작은 시작 유닉스 타임을 가진 행은 모두 제거(1시간 데이터만 보관)
    movement = movement[movement.start_unix > fsec - self.subtractor // 2]
movement['start_unix'] = movement['start_unix'].astype(int)
self.movement = movement.reset_index(drop=True)
display(self.movement.head())

In [13]:
self.update_movement()

In [14]:
# 4-1
self.merge_dfs()

In [15]:
# 4-2
self.assign_signals()

In [16]:
# 4-3
self.attach_children()

In [17]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(self.histids)

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         457  106234  1722383873       1       1       6       2        45   
1         457  106234  1722383873       2       2       5       1        20   
2         457  106234  1722383873       3       3      17      17        40   
3         457  106234  1722383873       4       4       8       3        35   
4         457  106234  1722383873       5       5       7       4        40   
5         456  106231  1722383877       1       1       5       2        15   
6         456  106231  1722383877       2       2       6       2        28   
7         456  106231  1722383877       3       3       7       7        12   
8         456  106231  1722383877       4       4      17      17        35   
9         455  109901  1722383886       1       1       6       2        63   
10        442  106332  1722383898       1       1       6       1        31   
11        442  106332  1722383898       2       2       6       2        27   
12        442  106332  1722383898       3       3       5       2        32   
13        442  106332  1722383898       4       4       7       4        49   
14        442  106332  1722383898       5       5       8       3        45   
15        442  106332  1722383898       6       6       8       3        16   
16        443  108769  1722383902       1       1       6       2       125   
17        443  108769  1722383902       2       2       5       2        25   
18        443  108769  1722383902       3       3       7      18        50   
19        456  106231  1722383967       1       1       5       2        15   
20        456  106231  1722383967       2       2       6       2        28   
21        456  106231  1722383967       3       3       7      -1        12   
22        456  106231  1722383967       4       4      17      -1        35   
23        456  106231  1722383968       1       1       5       2        15   
24        456  106231  1722383968       2       2       6       2        28   
25        456  106231  1722383968       3       3       7       7        12   
26        456  106231  1722383968       4       4      17      17        35   
27        455  109901  1722383975       1       1       6       2        63   
28        455  109901  1722383976       1       1       6       2        63   
29        455  109901  1722383976       2       2      -1      -1        27   
30        437  109986  1722384007       1       1       6       2        77   
31        437  109986  1722384007       2       2       5       1        28   
32        437  109986  1722384007       3       3       8       3        46   
33        437  109986  1722384007       4       4       7       4        49   
34        436  109836  1722384036       1       1       5       2        50   
35        436  109836  1722384036       2       2       8       3        85   
36        436  109836  1722384036       3       3       7       4        35   
37        436  109836  1722384036       4       4       6       1        30   
38        457  106234  1722384052       1       1       6       2        45   
39        457  106234  1722384052       2       2       5       1        20   
40        457  106234  1722384052       3       3      17      17        40   
41        457  106234  1722384052       4       4       8       3        40   
42        457  106234  1722384052       5       5       7       4        35   
43        456  106231  1722384057       1       1       5       2        15   
44        456  106231  1722384057       2       2       6       2        28   
45        456  106231  1722384057       3       3       7       7        12   
46        456  106231  1722384057       4       4      17      17        35   
47        456  106231  1722384058       1       1       5       2        15   
48        456  106231  1722384058       2       2       6       2        28   
49        456  106231  1722384058       3       3      

In [18]:
# 5-1
self.set_timepoints()

In [24]:
self.node_ids

['106231',
 '106234',
 '106238',
 '106332',
 '106350',
 '108769',
 '109836',
 '109901',
 '109986']

In [23]:
self.uturn_ids

['107587', '109295', '109296', '109297', '109313', '109333']

In [21]:
len(self.parent_ids)

9

In [19]:
# 5-2. 적색 및 황색신호 부여
self.assign_red_yellow()

c:\github\siggen\scripts\generate_signals.py:801: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  SIG[['phas_A', 'state_A']] = SIG[['phas_A', 'state_A']].fillna(method='ffill')
c:\github\siggen\scripts\generate_signals.py:802: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  SIG[['phas_B', 'state_B']] = SIG[['phas_B', 'state_B']].fillna(method='ffill')
c:\github\siggen\scripts\generate_signals.py:801: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  SIG[['phas_A', 'state_A']] = SIG[['phas_A', 'state_A']].fillna(method='ffill')
c:\github\siggen\scripts\generate_signals.py:802: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  SIG[['phas_

KeyError: "Only a column name can be used for the key in a dtype mappings argument. 'red_A' not found in columns."